# DataRobotのベクターデータベースを作成およびデプロイする

このノートブックでは、DataRobotに組み込まれた埋め込みモデルを用いたベクターデータベース（VDB）を、DataRobot Python SDKを使用して作成し、デプロイする方法について説明します。これはベクターデータベースの作成において最も簡単な手法であり、カスタムモデルを作成する必要はありません。独自の埋め込みモデル（BYO埋め込み）を使用する必要がある場合は、[BYO埋め込みからのベクターデータベースの作成](create-vdb-byo-embedding.ipynb)ノートブックに詳細な例があります。このワークフロー例では以下のことを行います。


- ユースケースを作成し、データセットをアップロードします。

- ドキュメントにチャンキングパラメーターを設定します。

- DataRobotに組み込まれた埋め込みモデルを使用して、ベクターデータベースを作成します。

- 本番環境で使用するベクターデータベースをデプロイします。


**注**：セルフマネージドAIプラットフォームでは、`app.datarobot.com`を参照するコードサンプルは、インスタンスに適したURLに変更する必要があります。


## セットアップ

### 前提条件

このワークフローでは以下の機能フラグが必要です。これらの機能を有効にするには、DataRobotの担当者または管理者にお問い合わせください。


- Enable MLOps

- すべてのカスタムモデルでパブリックネットワークへのアクセスを有効にする（プレミアム）

- 生成モデルの監視サポートを有効にする

- Enable Custom Inference Models

- Enable GenAI Experimentation


### ライブラリのインポート
このセクションでは、DataRobotとの対話、ドキュメントチャンキングの設定、ベクターデータベースの作成とデプロイの管理に必要なPythonライブラリをインポートします。これらのライブラリは、ワークフローの接続、設定、オーケストレーションに必要なインターフェイスを提供します。


In [ ]:
import datarobot as dr
from datarobot.models.genai.vector_database import VectorDatabase
from datarobot.models.genai.vector_database import ChunkingParameters
from datarobot.enums import VectorDatabaseEmbeddingModel
from datarobot.enums import VectorDatabaseChunkingMethod
from datarobot.enums import PredictionEnvironmentPlatform
from datarobot.enums import PredictionEnvironmentModelFormats
import time
import requests

### DataRobotに接続する

このセクションでは、DataRobotクライアントへの接続を管理しました。[PythonクライアントからDataRobotに接続する](https://docs.datarobot.com/ja/docs/api/api-quickstart/api-qs.html)ための各オプションの詳細をご確認ください。


In [ ]:
# Option 1: Use environment variables (recommended)
# The client will automatically use DATAROBOT_ENDPOINT and DATAROBOT_API_TOKEN
dr.Client()

# Option 2: Explicitly provide endpoint and token
# endpoint = "https://app.datarobot.com/api/v2"
# token = "<ADD_YOUR_TOKEN_HERE>"
# dr.Client(endpoint=endpoint, token=token)

## DataRobotに組み込まれた埋め込みモデルを使用してベクターデータベースを作成する

このアプローチでは、DataRobotに組み込まれた埋め込みモデルを使用して、アップロードされたドキュメントからベクターデータベースを作成およびデプロイします。


### ユースケースの取得

ベクターデータベースは、DataRobotのユースケースに関連付ける必要があります。この手順では、ノートブックが実行されているユースケース (使用可能な場合) を使用するか、ノートブックがユースケースに含まれていない場合は新しいユースケースを作成します。より具体的なユースケース名を定義するには、`USE_CASE_NAME`を設定します。


In [ ]:
# Create the Use Case
USE_CASE_NAME = "VDB Example Use Case"
use_case = dr.UseCase.create(name=USE_CASE_NAME)
print(f"Created Use Case: {use_case.name}")

### データセットのアップロード

このセクションでは、ドキュメントデータセットをアップロードします。データセットは、テキストファイル（`.txt`、`.md`など）を含むZIPファイルである必要があります。各ファイルはベクターデータベース用に処理され、チャンク化されます。


In [ ]:
# Get or create the dataset
DATASET_NAME = "pirate_resumes.zip"
dataset = None

# Search for existing dataset by exact name
try:
    all_datasets = dr.Dataset.list(filter_failed=True)
    for d in all_datasets:
        if d.name == DATASET_NAME:
            dataset = d
            print(f"Found existing dataset: {dataset.name}")
            break
except Exception:
    pass

# Upload if not found
if not dataset:
    dataset_url = "https://s3.amazonaws.com/datarobot_public_datasets/genai/pirate_resumes.zip"
    dataset = dr.Dataset.create_from_url(dataset_url)
    print(f"Uploaded new dataset: {dataset.name}")

# Add dataset to Use Case if not already added
try:
    use_case_datasets = use_case.get_datasets()
    dataset_ids = [d.id for d in use_case_datasets]
    if dataset.id not in dataset_ids:
        use_case.add(dataset)
        print(f"Added dataset to Use Case")
except Exception:
    pass  # Already added or error adding

### チャンキングパラメーターの設定

ドキュメントをチャンクに分割する方法を設定します。チャンキングパラメーターによって、以下のことが決まります。


- **チャンクサイズ**：1つのチャンクあたりの最大文字数。

- **チャンクオーバーラップ**：チャンク間の重複率（コンテキストの維持に役立ちます）。

- **チャンキング手法**：テキストの分割に使用されるアルゴリズム（再帰、固定など）。

- **埋め込みモデル**：埋め込みの生成に使用されるモデル（オプション、デフォルトはJina）。


In [ ]:
chunking_parameters = ChunkingParameters(
    embedding_model=VectorDatabaseEmbeddingModel.JINA_EMBEDDING_T_EN_V1,
    chunking_method=VectorDatabaseChunkingMethod.RECURSIVE,
    chunk_size=256,
    chunk_overlap_percentage=25,
    separators=["\n\n", "\n", " ", ""],
)

### ベクターデータベースの作成

データセットとチャンキングパラメーターを使ってベクターデータベースを作成します。このプロセスでは以下の処理が行われます。


1. ドキュメントをチャンクに分割します。

2. 指定された埋め込みモデルを使用して、各チャンクに埋め込みを生成します。

3. チャンクと埋め込みをベクターデータベースに保存します。


このプロセスは、データセットのサイズに応じて、通常30〜60秒かかります。


In [ ]:
vdb = VectorDatabase.create(
    dataset_id=dataset.id,
    chunking_parameters=chunking_parameters,
    use_case=use_case,
    name="My Vector Database"
)

正常に完了するまで、ベクターデータベースのステータスをチェックします。


In [ ]:
max_wait_time = 600
check_interval = 5
start_time = time.time()

print("Waiting for vector database creation...")
while time.time() - start_time < max_wait_time:
    vdb = VectorDatabase.get(vdb.id)
    status = vdb.execution_status
    if status == "COMPLETED":
        print(f"Vector database created: {vdb.name}")
        break
    elif status == "FAILED":
        error_msg = getattr(vdb, 'error_message', 'Unknown error')
        raise Exception(f"Vector database creation failed: {error_msg}")
    else:
        # Show progress if available
        percentage = getattr(vdb, 'percentage', None)
        if percentage is not None:
            print(f"  Status: {status} ({percentage}%)")
        else:
            print(f"  Status: {status}...")
    time.sleep(check_interval)
else:
    raise Exception(f"Vector database creation timed out after {max_wait_time} seconds")

assert vdb.execution_status == "COMPLETED", f"Vector database creation failed with status: {vdb.execution_status}"

## ベクターデータベースのデプロイ

ベクターデータベースが作成されたら、本番環境で使用するためにデプロイします。ベクターデータベースのデプロイには、主に2つの方法があります。


* **直接デプロイ**：Python SDKを使用してベクターデータベースを予測環境に直接デプロイします。

* **ワークショップに送る**：最初にベクターデータベースをカスタムモデルとして登録してから、デプロイします。


### 予測環境の作成

まず、予測環境が必要です。DataRobotサーバーレスは通常、ベクターデータベースのデプロイに使用されます。このセクションでは、予測環境がまだ存在しない場合に新規に作成します。さらに、ベクターデータベースの実行に必要なリソースバンドルを選択します。


In [ ]:
PREDICTION_ENVIRONMENT_NAME = "Vector Database Prediction Environment"

# Get or create prediction environment
prediction_environment = None
for env in dr.PredictionEnvironment.list():
    if env.name == PREDICTION_ENVIRONMENT_NAME:
        prediction_environment = env
        break

if prediction_environment is None:
    prediction_environment = dr.PredictionEnvironment.create(
        name=PREDICTION_ENVIRONMENT_NAME,
        platform=PredictionEnvironmentPlatform.DATAROBOT_SERVERLESS,
        supported_model_formats=[
            PredictionEnvironmentModelFormats.DATAROBOT,
            PredictionEnvironmentModelFormats.CUSTOM_MODEL
        ],
    )
    print(f"Created prediction environment: {prediction_environment.name}")
else:
    print(f"Using existing prediction environment: {prediction_environment.name}")

# Select 3XL resource bundle
resource_bundle_id = None
try:
    dr_client = dr.Client()
    bundles_url = f"{dr_client.endpoint}/mlops/compute/bundles/"
    headers = {"Authorization": f"Bearer {dr_client.token}"}
    bundles_response = requests.get(bundles_url, headers=headers, params={"useCases": "customModel"})
    
    if bundles_response.status_code == 200:
        bundles_data = bundles_response.json()
        if bundles_data.get("data"):
            bundles = bundles_data["data"]
            # Look for 3XL bundle
            bundle_3xl = next((b for b in bundles if "3XL" in b.get("name", "").upper()), None)
            if bundle_3xl:
                resource_bundle_id = bundle_3xl["id"]
                print(f"Selected 3XL bundle: {bundle_3xl['name']}")
            else:
                # Fallback to largest available
                sorted_bundles = sorted(bundles, key=lambda b: b.get("memoryBytes", 0), reverse=True)
                if sorted_bundles:
                    resource_bundle_id = sorted_bundles[0]["id"]
                    print(f"Warning: 3XL bundle not found. Using largest available: {sorted_bundles[0]['name']}")
        else:
            print("Using memory settings (no resource bundles available)")
    else:
        print("Using memory settings (resource bundles not enabled)")
except (ImportError, KeyError) as e:
    print(f"Using memory settings (error checking bundles): {e}")
except requests.RequestException as e:
    print(f"Using memory settings (network error checking bundles): {e}")

### ベクターデータベースをワークショップに送信する

デプロイする前に、ベクターデータベースをカスタムモデルワークショップに送信します。これにより、登録およびデプロイが可能なカスタムモデルのバージョンが作成されます。


このコードは、予測環境の作成時または確認時に決定されたリソース設定（利用可能な場合はリソースバンドル、それ以外の場合はメモリー設定）を使用します。


In [ ]:
assert vdb.execution_status == "COMPLETED", f"Vector database must be completed. Current status: {vdb.execution_status}"

# Send to workshop with 3XL bundle or memory settings
if resource_bundle_id:
    custom_model_version = vdb.send_to_custom_model_workshop(
        resource_bundle_id=resource_bundle_id,
        replicas=1,
        network_egress_policy=dr.NETWORK_EGRESS_POLICY.PUBLIC,
    )
else:
    custom_model_version = vdb.send_to_custom_model_workshop(
        maximum_memory=4096*1024*1024,
        replicas=1,
        network_egress_policy=dr.NETWORK_EGRESS_POLICY.PUBLIC,
    )

print(f"Custom model version created: {custom_model_version}")

### モデルの登録

次に、カスタムモデルのバージョンを登録します。同じ名前で登録されたモデルがすでに存在する場合、この手順では、複製を作成する代わりに、既存のモデルに新しいバージョンを追加します。



In [ ]:
REGISTERED_MODEL_NAME = f"Vector Database - {vdb.name}"

# Register model (adds new version if model already exists)
existing_models = [m for m in dr.RegisteredModel.list() if m.name == REGISTERED_MODEL_NAME]

if existing_models:
    registered_model_version = dr.RegisteredModelVersion.create_for_custom_model_version(
        custom_model_version_id=custom_model_version.id,
        registered_model_id=existing_models[0].id,
    )
    print(f"Added new version to existing registered model: {REGISTERED_MODEL_NAME}")
else:
    registered_model_version = dr.RegisteredModelVersion.create_for_custom_model_version(
        custom_model_version_id=custom_model_version.id,
        registered_model_name=REGISTERED_MODEL_NAME,
    )
    print(f"Created new registered model: {REGISTERED_MODEL_NAME}")


### モデル構築の完了を待つ

登録モデルのバージョンが構築されるのを待ってから、デプロイします。



In [ ]:
registered_model = dr.RegisteredModel.get(registered_model_version.registered_model_id)
max_wait_time = 600
check_interval = 10
start_time = time.time()

print("Waiting for model build to complete...")
while time.time() - start_time < max_wait_time:
    version = registered_model.get_version(registered_model_version.id)
    build_status = getattr(version, 'build_status', None) or getattr(version, 'buildStatus', None)
    
    if build_status in ('READY', 'complete', 'COMPLETE'):
        print(f"Model build completed (status: {build_status})")
        break
    elif build_status in ('FAILED', 'ERROR', 'error'):
        raise Exception(f"Model build failed. Status: {build_status}")
    else:
        print(f"  Build status: {build_status}...")
    time.sleep(check_interval)
else:
    version = registered_model.get_version(registered_model_version.id)
    build_status = getattr(version, 'build_status', None) or getattr(version, 'buildStatus', None)
    raise Exception(f"Model build timed out. Current status: {build_status}")

# Verify ready status
version = registered_model.get_version(registered_model_version.id)
final_status = getattr(version, 'build_status', None) or getattr(version, 'buildStatus', None)
if final_status not in ('READY', 'complete', 'COMPLETE'):
    raise Exception(f"Model not ready for deployment. Status: {final_status}")


### 登録されたモデルのデプロイ

登録モデルのバージョンを、先に作成した予測環境にデプロイします。デプロイ処理を正常に終了するには、モデルが準備完了状態である必要があります。



In [ ]:

deployment = dr.Deployment.create_from_registered_model_version(
    registered_model_version.id,
    label=f"Vector Database Deployment - {vdb.name}",
    description="Vector database deployment for RAG applications",
    prediction_environment_id=prediction_environment.id,
    max_wait=600,
)

print(f"Deployment created: {deployment.id}")


### LLMプレイグラウンドでベクターデータベースを使う

Python SDKで作成されたベクターデータベースは、LLMプレイグラウンドで自動的に使用可能になり、RAGワークフローで使えます。LLMでベクターデータベースを使用する例については、[genai-e2e.ipynb](genai-e2e.ipynb)ノートブックを参照してください。


デプロイ手順とUIオプションの詳細については、[ベクターデータベースの登録とデプロイ](https://docs.datarobot.com/ja/docs/gen-ai/vector-database/vector-dbs-register-deploy.html)に関するドキュメントを参照してください。


## ベクターデータベースの一覧表示と管理

以下のコマンドを使用して、ユースケースに関連付けられているすべてのベクターデータベースを一覧表示し、プログラムによって管理します。


In [ ]:
# List all vector databases in a Use Case
vdbs = VectorDatabase.list(use_case=use_case)
print(f"Found {len(vdbs)} vector database(s) in Use Case '{use_case.name}'")

### 以降のステップ：

- [LLMプレイグラウンド](genai-e2e.ipynb)でベクターデータベースを使用します。

- [カスタム埋め込みモデルによるベクターデータベースの作成](create-vdb-byo-embedding.ipynb)（BYO埋め込み）について紹介します。

- ChromaDBのような[外部ベクターデータベース](chromadb-vdb.ipynb)を探索します。
